In [11]:
import pandas as pd 
import numpy as np
import re
import os
import math

In [4]:
with open("/Users/bowiechuang/Documents/GitHub/ProjectNexus/backend/emails.csv", "r") as f:
    for i in range(10):
        print(repr(f.readline()))

'"file","message"\n'
'"allen-p/_sent_mail/1.","Message-ID: <18782981.1075855378110.JavaMail.evans@thyme>\n'
'Date: Mon, 14 May 2001 16:39:00 -0700 (PDT)\n'
'From: phillip.allen@enron.com\n'
'To: tim.belden@enron.com\n'
'Subject: \n'
'Mime-Version: 1.0\n'
'Content-Type: text/plain; charset=us-ascii\n'
'Content-Transfer-Encoding: 7bit\n'
'X-From: Phillip K Allen\n'


In [6]:

def iter_email_batches(path, batch_size=5000):
    row_start = re.compile(r'^"[^"]+","')
    records = []
    current_file = None
    current_msg_lines = []

    with open(path, "r", encoding="utf-8", errors="replace") as f:
        f.readline()  # skip header

        for line in f:
            if row_start.match(line):
                if current_file is not None:
                    records.append({"file": current_file, "message": "".join(current_msg_lines)})

                first_comma = line.find('","')
                current_file = line[1:first_comma]
                current_msg_lines = [line[first_comma + 3:]]

                if len(records) >= batch_size:
                    yield pd.DataFrame(records)
                    records = []
            else:
                if current_file is not None:
                    current_msg_lines.append(line)

    if current_file is not None:
        records.append({"file": current_file, "message": "".join(current_msg_lines)})

    if records:
        yield pd.DataFrame(records)

# usage:
path = "/Users/bowiechuang/Documents/GitHub/ProjectNexus/backend/emails.csv"
dfs = []
for df_chunk in iter_email_batches(path, batch_size=5000):
    dfs.append(df_chunk)

df_email = pd.concat(dfs, ignore_index=True)

In [7]:
df_email

file  \
0           allen-p/_sent_mail/1.   
1          allen-p/_sent_mail/10.   
2         allen-p/_sent_mail/100.   
3        allen-p/_sent_mail/1000.   
4        allen-p/_sent_mail/1001.   
...                           ...   
517396  zufferli-j/sent_items/95.   
517397  zufferli-j/sent_items/96.   
517398  zufferli-j/sent_items/97.   
517399  zufferli-j/sent_items/98.   
517400  zufferli-j/sent_items/99.   

                                                  message  
0       Message-ID: <18782981.1075855378110.JavaMail.e...  
1       Message-ID: <15464986.1075855378456.JavaMail.e...  
2       Message-ID: <24216240.1075855687451.JavaMail.e...  
3       Message-ID: <13505866.1075863688222.JavaMail.e...  
4       Message-ID: <30922949.1075863688243.JavaMail.e...  
...                                                   ...  
517396  Message-ID: <26807948.1075842029936.JavaMail.e...  
517397  Message-ID: <25835861.1075842029959.JavaMail.e...  
517398  Message-ID: <28979867.1075842029988.JavaMail.e...  
517399  Message-ID: <22052556.1075842030013.JavaMail.e...  
517400  Message-ID: <28618979.1075842030037.JavaMail.e...  

[517401 rows x 2 columns]

In [9]:
df_email['message'].iloc[50]

'Message-ID: <27936946.1075855378542.JavaMail.evans@thyme>\nDate: Wed, 2 May 2001 10:27:00 -0700 (PDT)\nFrom: phillip.allen@enron.com\nTo: tori.kuykendall@enron.com\nSubject: Re: 2- SURVEY - PHILLIP ALLEN\nMime-Version: 1.0\nContent-Type: text/plain; charset=us-ascii\nContent-Transfer-Encoding: 7bit\nX-From: Phillip K Allen\nX-To: Tori Kuykendall <Tori Kuykendall/HOU/ECT@ECT>\nX-cc: \nX-bcc: \nX-Folder: \\Phillip_Allen_Jan2002_1\\Allen, Phillip K.\\\'Sent Mail\nX-Origin: Allen-P\nX-FileName: pallen (Non-Privileged).pst\n\n\n---------------------- Forwarded by Phillip K Allen/HOU/ECT on 05/02/2001 05:26 AM ---------------------------\n\n\nIna Rangel\n05/01/2001 12:24 PM\nTo:\tPhillip K Allen/HOU/ECT@ECT\ncc:\t \nSubject:\tRe: 2- SURVEY - PHILLIP ALLEN   \n\n\n\n\n   \n-\nFull Name:        Phillip Allen\n\nLogin ID:  \tpallen\n\nExtension:  3-7041\n\nOffice Location:  EB3210C\n\nWhat type of computer do you have?  (Desktop,  Laptop,  Both)  Both\n\nDo you have a PDA?  If yes, what type d

In [12]:
out_dir = "/Users/bowiechuang/Documents/GitHub/ProjectNexus/backend/email_chunks"
os.makedirs(out_dir, exist_ok=True)

chunk_size = 100_000
n_rows = len(df_email)
n_chunks = math.ceil(n_rows / chunk_size)

for i in range(n_chunks):
    start = i * chunk_size
    end = min((i + 1) * chunk_size, n_rows)

    df_chunk = df_email.iloc[start:end]

    out_path = os.path.join(out_dir, f"emails_part_{i+1}.parquet")
    df_chunk.to_parquet(out_path, index=False)

    print(f"Saved {out_path} ({len(df_chunk)} rows)")


Saved /Users/bowiechuang/Documents/GitHub/ProjectNexus/backend/email_chunks/emails_part_1.parquet (100000 rows)
Saved /Users/bowiechuang/Documents/GitHub/ProjectNexus/backend/email_chunks/emails_part_2.parquet (100000 rows)
Saved /Users/bowiechuang/Documents/GitHub/ProjectNexus/backend/email_chunks/emails_part_3.parquet (100000 rows)
Saved /Users/bowiechuang/Documents/GitHub/ProjectNexus/backend/email_chunks/emails_part_4.parquet (100000 rows)
Saved /Users/bowiechuang/Documents/GitHub/ProjectNexus/backend/email_chunks/emails_part_5.parquet (100000 rows)
Saved /Users/bowiechuang/Documents/GitHub/ProjectNexus/backend/email_chunks/emails_part_6.parquet (17401 rows)


### Epstein Txt Data

In [22]:
import re
import pandas as pd
import json

file_path = "/Users/bowiechuang/Documents/GitHub/ProjectNexus/backend/epstein_emails_insights_all.txt"

with open(file_path, "r", encoding="utf-8", errors="ignore") as f:
    raw_text = f.read()


In [14]:
records = re.split(r'(?="source_file":)', raw_text)
records = [r.strip() for r in records if r.strip()]
records

['[\n  {',
 '"source_file": "TEXT/001/HOUSE_OVERSIGHT_016595.txt",\n    "subject": "Re: ARCOM",\n    "date": "2008-06-26",\n    "participants": [\n      "Kirk Blouin",\n      "John Page",\n      "Tim Frank",\n      "Ray Royce",\n      "Rob Walton",\n      "Sgt. Krauel",\n      "Mr. Randolph",\n      "Mr. Fried",\n      "Ms. Van Buren"\n    ],\n    "people_mentioned": [\n      "Kirk Blouin",\n      "John Page",\n      "Rob Walton",\n      "Abe Gosman",\n      "Ray Royce",\n      "Mr. Randolph",\n      "Tim Frank",\n      "Mr. Trump",\n      "Mr. Fried",\n      "Ms. Van Buren",\n      "Sgt. Krauel"\n    ],\n    "notable_figures": [\n      "Donald Trump"\n    ],\n    "organizations": [\n      "Trump Properties LLC",\n      "Town of Palm Beach",\n      "Architectural Commission",\n      "Code Enforcement Board",\n      "ARCOM"\n    ],\n    "locations": [\n      "515 N. County Road",\n      "Palm Beach",\n      "North County Road"\n    ],\n    "summary": "The email conversation discusses a 

In [15]:
def extract_field(pattern, text, default=None, flags=re.DOTALL):
    match = re.search(pattern, text, flags)
    return match.group(1).strip() if match else default

In [16]:
parsed_rows = []

for rec in records:
    row = {
        "source_file": extract_field(r'"source_file":\s*"([^"]+)"', rec),
        "subject": extract_field(r'"subject":\s*"([^"]*)"', rec),
        "date": extract_field(r'"date":\s*"([^"]*)"', rec),
        "summary": extract_field(r'"summary":\s*"([^"]*)"', rec),
        "primary_topic": extract_field(r'"primary_topic":\s*"([^"]*)"', rec),
        "tone": extract_field(r'"tone":\s*"([^"]*)"', rec),
        "email_text": extract_field(r'"email_text":\s*"(.+?)"\s*(?:,|\n})', rec),
    }

    # Lists (participants, people_mentioned, organizations, locations)
    for field in ["participants", "people_mentioned", "organizations", "locations", "topics"]:
        list_match = extract_field(rf'"{field}":\s*\[(.*?)\]', rec)
        if list_match:
            row[field] = [x.strip().strip('"') for x in list_match.split(",")]
        else:
            row[field] = []

    parsed_rows.append(row)

In [17]:
df = pd.DataFrame(parsed_rows)

print(df.shape)
df.head()

(2323, 12)


source_file  \
0                                 None   
1  TEXT/001/HOUSE_OVERSIGHT_016595.txt   
2  TEXT/001/HOUSE_OVERSIGHT_016690.txt   
3  TEXT/001/HOUSE_OVERSIGHT_016553.txt   
4  TEXT/001/HOUSE_OVERSIGHT_016693.txt   

                                     subject        date  \
0                                       None        None   
1                                  Re: ARCOM  2008-06-26   
2                                  Re: ARCOM  2008-06-26   
3  Items for August 11 Town Council Meeting.  2008-07-24   
4                                Trump house  2008-11-19   

                                             summary primary_topic     tone  \
0                                               None          None     None   
1  The email conversation discusses a code enforc...   real_estate  routine   
2  The email conversation discusses ongoing code ...   real_estate  routine   
3  The participants are discussing agenda items f...   real_estate  routine   
4  The participants are discussing the correct ad...   real_estate  routine   

  email_text                                       participants  \
0       None                                                 []   
1       None  [Kirk Blouin, John Page, Tim Frank, Ray Royce,...   
2       None  [Kirk Blouin, John Page, Police Code Enforceme...   
3       None     [Anne Boyles, Cheryl Kleen, Kathleen Ruderman]   
4       None                                        [John Page]   

                                    people_mentioned  \
0                                                 []   
1  [Kirk Blouin, John Page, Rob Walton, Abe Gosma...   
2  [Kirk Blouin, John Page, Rob Walton, Royce, Ab...   
3  [Anne Boyles, Cheryl Kleen, Kathleen Ruderman,...   
4                         [John Page, Trump, Gosman]   

                                       organizations  \
0                                                 []   
1  [Trump Properties LLC, Town of Palm Beach, Arc...   
2  [Trump Properties LLC, Town of Palm Beach, Arc...   
3                                     [Town Council]   
4                                                 []   

                                           locations  \
0                                                 []   
1  [515 N. County Road, Palm Beach, North County ...   
2  [515 N. County Road, Palm Beach, North County ...   
3            [144 Wells Road, 515 North County Road]   
4     [515 North County Road, North Ocean Boulevard]   

                           topics  
0                              []  
1            [real_estate, legal]  
2  [real_estate, legal, business]  
3            [real_estate, legal]  
4                   [real_estate]

In [20]:
df

source_file  \
0                                    None   
1     TEXT/001/HOUSE_OVERSIGHT_016595.txt   
2     TEXT/001/HOUSE_OVERSIGHT_016690.txt   
3     TEXT/001/HOUSE_OVERSIGHT_016553.txt   
4     TEXT/001/HOUSE_OVERSIGHT_016693.txt   
...                                   ...   
2318  TEXT/001/HOUSE_OVERSIGHT_029504.txt   
2319  TEXT/001/HOUSE_OVERSIGHT_016203.txt   
2320  TEXT/001/HOUSE_OVERSIGHT_028801.txt   
2321  TEXT/001/HOUSE_OVERSIGHT_025792.txt   
2322  TEXT/001/HOUSE_OVERSIGHT_023107.txt   

                                                subject        date  \
0                                                  None        None   
1                                             Re: ARCOM  2008-06-26   
2                                             Re: ARCOM  2008-06-26   
3             Items for August 11 Town Council Meeting.  2008-07-24   
4                                           Trump house  2008-11-19   
...                                                 ...         ...   
2318                                                     2019-07-10   
2319                           11 questions for Mueller  2019-07-13   
2320  Alex Acosta resigns, Jeffrey Epstein arrested ...  2019-07-13   
2321                         Is Denmark going bankrupt?  2019-07-14   
2322  On the frontlines of the world's most stressfu...  2019-07-16   

                                                summary primary_topic  \
0                                                  None          None   
1     The email conversation discusses a code enforc...   real_estate   
2     The email conversation discusses ongoing code ...   real_estate   
3     The participants are discussing agenda items f...   real_estate   
4     The participants are discussing the correct ad...   real_estate   
...                                                 ...           ...   
2318  The email is a personal message from an indivi...      personal   
2319  The email is a newsletter-style communication ...      media_pr   
2320  The email is a newsletter style update sent to...         legal   
2321  The email thread consists of an automated Quor...         other   
2322  The email is an automated newsletter from Flip...         other   

          tone email_text                                       participants  \
0         None       None                                                 []   
1      routine       None  [Kirk Blouin, John Page, Tim Frank, Ray Royce,...   
2      routine       None  [Kirk Blouin, John Page, Police Code Enforceme...   
3      routine       None     [Anne Boyles, Cheryl Kleen, Kathleen Ruderman]   
4      routine       None                                        [John Page]   
...        ...        ...                                                ...   
2318  informal       None                                  [Jeffrey Epstein]   
2319   routine       None                                  [Jeffrey Epstein]   
2320   routine       None                                  [Jeffrey Epstein]   
2321   routine       None                                  [Jeffrey Epstein]   
2322   routine       None                                  [Jeffrey Epstein]   

                                       people_mentioned  \
0                                                    []   
1     [Kirk Blouin, John Page, Rob Walton, Abe Gosma...   
2     [Kirk Blouin, John Page, Rob Walton, Royce, Ab...   
3     [Anne Boyles, Cheryl Kleen, Kathleen Ruderman,...   
4                            [John Page, Trump, Gosman]   
...                                                 ...   
2318                   [Jeffrey Epstein, Prince Andrew]   
2319  [Robert Mueller, Stephanie Grisham, John F. Ke...   
2320  [Alex Acosta, Jeffrey Epstein, Tom Steyer, Ros...   
2321  [Erik Callaway, Parth Parulekar, Jill Grant, E...   
2322  [Darcy Frey, Johanna Walderdorff, Frances Nort...   

                                          organizations  \
0                             

In [23]:
path = "/Users/bowiechuang/Documents/GitHub/ProjectNexus/backend/epstein_emails_insights_all.txt"

with open(path, "r", encoding="utf-8") as f:
    data = json.load(f)   # list[dict]

df = pd.DataFrame(data)

print(df.shape)                 # should be ~2000+ rows
print(df["email_text"].notna().sum())
df.head()

(2322, 18)
2322


source_file  \
0  TEXT/001/HOUSE_OVERSIGHT_016595.txt   
1  TEXT/001/HOUSE_OVERSIGHT_016690.txt   
2  TEXT/001/HOUSE_OVERSIGHT_016553.txt   
3  TEXT/001/HOUSE_OVERSIGHT_016693.txt   
4  TEXT/001/HOUSE_OVERSIGHT_030992.txt   

                                       subject        date  \
0                                    Re: ARCOM  2008-06-26   
1                                    Re: ARCOM  2008-06-26   
2    Items for August 11 Town Council Meeting.  2008-07-24   
3                                  Trump house  2008-11-19   
4  Fwd: FW: As Obama says "We've got problems"  2009-04-14   

                                        participants  \
0  [Kirk Blouin, John Page, Tim Frank, Ray Royce,...   
1  [Kirk Blouin, John Page, Police Code Enforceme...   
2     [Anne Boyles, Cheryl Kleen, Kathleen Ruderman]   
3                                        [John Page]   
4                                  [Jeffrey Epstein]   

                                    people_mentioned  \
0  [Kirk Blouin, John Page, Rob Walton, Abe Gosma...   
1  [Kirk Blouin, John Page, Rob Walton, Royce, Ab...   
2  [Anne Boyles, Cheryl Kleen, Kathleen Ruderman,...   
3                         [John Page, Trump, Gosman]   
4                                  [Osama Bin-Laden]   

                   notable_figures  \
0                   [Donald Trump]   
1                   [Donald Trump]   
2                   [Donald Trump]   
3                   [Donald Trump]   
4  [Barack Obama, Osama Bin-Laden]   

                                       organizations  \
0  [Trump Properties LLC, Town of Palm Beach, Arc...   
1  [Trump Properties LLC, Town of Palm Beach, Arc...   
2                                     [Town Council]   
3                                                 []   
4  [federal government, state and city Government...   

                                           locations  \
0  [515 N. County Road, Palm Beach, North County ...   
1  [515 N. County Road, Palm Beach, North County ...   
2            [144 Wells Road, 515 North County Road]   
3     [515 North County Road, North Ocean Boulevard]   
4                                          [America]   

                                             summary primary_topic  \
0  The email conversation discusses a code enforc...   real_estate   
1  The email conversation discusses ongoing code ...   real_estate   
2  The participants are discussing agenda items f...   real_estate   
3  The participants are discussing the correct ad...   real_estate   
4  The email conversation consists of Jeffrey Eps...         other   

                           topics      tone potential_crimes crime_types  \
0            [real_estate, legal]   routine                           []   
1  [real_estate, legal, business]   routine                           []   
2            [real_estate, legal]   routine                           []   
3                   [real_estate]   routine                           []   
4                         [other]  informal                           []   

   mentions_victims victim_names cover_up  \
0             False           []            
1             False           []            
2             False           []            
3             False           []            
4             False           []            

                                          email_text  
0  ﻿From:\nTo:\nCc:\nSubject:\nDate:\nKirk Blouin...  
1  ﻿From:\nTo:\nCc:\nSubject:\nDate:\nKirk Blouin...  
2  ﻿From:\nTo:\nSubject:\nDate:\nCN=Anne Boyles/O...  
3  From: \nTo: \nSubject: \nDate: \nJohn Page \nR...  
4  From: \nSent: \nTo: \nSubject: \nJeffrey Epste...

In [37]:
print(df['email_text'].iloc[10])

Date: Tuesday, June 23 2009 10:49 PM 
Subject: Re: Radar Online reports that you are to be released early 
From: Jeffrey Epstein <jeevacation@gmail.corn> 
To: David Grosof 
http://www.palmbeachdailynews.com/news/content/news/2009/06/23/webepstein062309.html  
On Sat, Jun 20, 2009 at 6:41 AM, Jeevacation <jeevacation(&,gmail.com> wrote: 
30 days 
Sent from my iPhone 
On Jun 20, 2009, at 4:01 AM, David Grosof 
wrote: 
Hi, Jeffrey, 
I hope the Radar Online report today (Friday 6-19) that you are to be released early is correct! 
Best wishes, 
David 
Referencing: 
http://www.radaronline.com/exclusives/2009/06/exclusive- jeffrey-epstein-be-released-prison- early 
EXCLUSIVE: Jeffrey Epstein To Be Released From Prison Early 
Jeffrey Epstein, the Florida money manager who once roamed in the same social circle as Bill Clinton, 
Prince Andrew and other high profile figures, is going to be released from prison early, a source tells 
RadarOnline.com. 
Epstein pleaded guilty last year to procuring 

In [24]:
def basic_clean(text):
    if not isinstance(text, str):
        return ""

    # Normalize line breaks
    text = text.replace("\r\n", "\n").replace("\r", "\n")

    # Remove excessive blank lines
    text = re.sub(r"\n{3,}", "\n\n", text)

    # Strip leading/trailing whitespace
    return text.strip()

def remove_inline_headers(text):
    lines = text.split("\n")
    cleaned = []

    header_patterns = re.compile(
        r"^(from|to|cc|bcc|subject|sent|date)\s*:",
        re.IGNORECASE
    )

    for line in lines:
        if header_patterns.match(line.strip()):
            continue
        cleaned.append(line)

    return "\n".join(cleaned)

def remove_quoted_replies(text):
    patterns = [
        r"-----original message-----.*",
        r"from:.*sent:.*to:.*subject:.*",
        r"on .* wrote:.*",
        r"^>.*",
    ]

    for p in patterns:
        text = re.sub(p, "", text, flags=re.IGNORECASE | re.DOTALL | re.MULTILINE)

    return text.strip()

def remove_signatures(text):
    signature_markers = [
        r"\n--\s*\n.*",          # standard signature separator
        r"\nthanks[,\s].*",
        r"\nbest[,\s].*",
        r"\nregards[,\s].*",
        r"\nsincerely[,\s].*",
    ]

    for p in signature_markers:
        text = re.sub(p, "", text, flags=re.IGNORECASE | re.DOTALL)

    return text.strip()

def clean_email_text(text):
    text = basic_clean(text)
    text = remove_inline_headers(text)
    text = remove_quoted_replies(text)
    text = remove_signatures(text)

    # Final whitespace cleanup
    text = re.sub(r"[ \t]+", " ", text)
    text = re.sub(r"\n{2,}", "\n\n", text)

    return text.strip()

In [29]:
df["email_text_clean"] = df["email_text"].str.replace("\n", "")
df['email_text_clean'].iloc[10]

"Date: Tuesday, June 23 2009 10:49 PM Subject: Re: Radar Online reports that you are to be released early From: Jeffrey Epstein <jeevacation@gmail.corn> To: David Grosof http://www.palmbeachdailynews.com/news/content/news/2009/06/23/webepstein062309.html  On Sat, Jun 20, 2009 at 6:41 AM, Jeevacation <jeevacation(&,gmail.com> wrote: 30 days Sent from my iPhone On Jun 20, 2009, at 4:01 AM, David Grosof wrote: Hi, Jeffrey, I hope the Radar Online report today (Friday 6-19) that you are to be released early is correct! Best wishes, David Referencing: http://www.radaronline.com/exclusives/2009/06/exclusive- jeffrey-epstein-be-released-prison- early EXCLUSIVE: Jeffrey Epstein To Be Released From Prison Early Jeffrey Epstein, the Florida money manager who once roamed in the same social circle as Bill Clinton, Prince Andrew and other high profile figures, is going to be released from prison early, a source tells RadarOnline.com. Epstein pleaded guilty last year to procuring teen girls for pros

In [32]:
df.to_csv("/Users/bowiechuang/Documents/GitHub/ProjectNexus/backend/epstein_email.csv", index = False)

### Enron Chain Email

In [33]:
thread_df = pd.read_csv("/Users/bowiechuang/Documents/GitHub/ProjectNexus/backend/chain_emil_final.csv")
thread_df

thread_id  \
0       <10000030.1075853224853.JavaMail.evans@thyme>   
1       <10000165.1075853973005.JavaMail.evans@thyme>   
2       <10000282.1075847198841.JavaMail.evans@thyme>   
3       <10000392.1075856574818.JavaMail.evans@thyme>   
4       <10000461.1075841331186.JavaMail.evans@thyme>   
...                                               ...   
234692   <9998633.1075861106901.JavaMail.evans@thyme>   
234693   <9998991.1075840855150.JavaMail.evans@thyme>   
234694   <9999243.1075842005692.JavaMail.evans@thyme>   
234695   <9999779.1075845232451.JavaMail.evans@thyme>   
234696   <9999931.1075852407238.JavaMail.evans@thyme>   

                                         subject  n_messages  avg_confidence  \
0                                   trial lawyer           1        0.832389   
1       personal information needs to be updated           1        0.695214   
2                  clickpaper approvals 09/27/00           1        0.517464   
3                               telerate service           1        0.813824   
4                                how's business?           1        0.884976   
...                                          ...         ...             ...   
234692                                    binder           1        0.617087   
234693                                       NaN           1        0.781815   
234694                         volume management           1        0.837335   
234695                                       NaN           1        0.713179   
234696                                       NaN           1        0.917627   

        majority_pred                                         chain_text  \
0                   0  ---\nDATE: 2001-06-04 23:43:00-07:00\nFROM: ri...   
1                   0  ---\nDATE: 2000-11-07 06:24:00-08:00\nFROM: he...   
2                   0  ---\nDATE: 2000-09-28 02:44:00-07:00\nFROM: ta...   
3                   0  ---\nDATE: 2001-03-29 03:00:00-08:00\nFROM: sh...   
4                   0  ---\nDATE: 2001-03-26 14:08:00-08:00\nFROM: pa...   
...               ...                                                ...   
234692              0  ---\nDATE: 2002-02-21 06:09:43-08:00\nFROM: al...   
234693              0  ---\nDATE: 2001-07-12 07:17:45-07:00\nFROM: da...   
234694              0  ---\nDATE: 2002-01-22 07:32:22-08:00\nFROM: w....   
234695              0  ---\nDATE: 2001-05-31 13:19:19-07:00\nFROM: jo...   
234696              0  ---\nDATE: 2001-10-24 08:34:29-07:00\nFROM: al...   

        prediction  confidence  
0                0    0.860543  
1                0    0.835549  
2                0    0.633859  
3                0    0.951806  
4                0    0.970837  
...            ...         ...  
234692           0    0.844020  
234693           0    0.874081  
234694           0    0.867329  
234695           0    0.717004  
234696           0    0.919051  

[234697 rows x 8 columns]

In [36]:
print(thread_df['chain_text'].iloc[20000])

---
DATE: 2001-05-07 09:37:00-07:00
FROM: eileen.ogrady@dowjones.com
TO: eileen.ogrady@dowjones.com
SUBJECT: FYI: The Ercot Story from 5/7 WSJ

Charged Up:
Texas May Face a Glut
Of Electricity, but That
Won't Aid Rest of U.S.
---
Pride and Policy Make State
A Magnet  for Power Plants
And an Island Unto Itself
---
A Wire Enshrined in Lucite
----
By Alexei Barrionuevo and Russell Gold
Staff Reporters of The Wall Street Journal

The Wall Street Journal via Dow Jones

While California struggles to keep its lights on and New York City braces
for
possible electricity shortages this summer, Texas utilities could soon face
the
opposite problem: a power glut.

Texas' wide-open spaces and relatively weak zoning and environmental rules
have helped make the Lone Star state a magnet for power-generation companies
as
it prepares to deregulate its electricity market next year. The result:
Texas'
electricity-production capacity this summer is expected to exceed its peak
power
demand by 11,000 megawatt